In [6]:
import pandas as pd

df = pd.read_csv("bills.csv")
df.head()

bill_name                                          bill_text
0  Louisiana-HB167  ENROLLED\n\nACT No. 2512020 Regular Session\nH...
1     izona-SB1003  8/2/2021 Arizona-2021-SB1003-Chaptered\n\nhttp...
2    kansas-HB1715  HB1715 as engrossed on 03-29-2021 11:52:30\n\n...
3   Wyoming-HB0075  21LSO-0192\n\n\nORIGINAL HOUSE ENGROSSED\nBILL...
4    Kansas hb2183  Senate Substitute for HOUSE BILL No. 2183\n\nA...

In [7]:
df = df.set_index('bill_name')
df.head()

bill_text
bill_name                                                         
Louisiana-HB167  ENROLLED\n\nACT No. 2512020 Regular Session\nH...
izona-SB1003     8/2/2021 Arizona-2021-SB1003-Chaptered\n\nhttp...
kansas-HB1715    HB1715 as engrossed on 03-29-2021 11:52:30\n\n...
Wyoming-HB0075   21LSO-0192\n\n\nORIGINAL HOUSE ENGROSSED\nBILL...
Kansas hb2183    Senate Substitute for HOUSE BILL No. 2183\n\nA...

In [8]:
df.shape

(27, 1)

### STEP ONE: Vectorize!

* We used Tfidf because it makes common phrases less important, and bills are full of common stock phrases like "I present to the speaker"
* We used ngram_range of (1,3) because... it seemed right? We can always change it later.

In [15]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(ngram_range=(2, 5))

matrix = vectorizer.fit_transform(df.bill_text)
words_df = pd.DataFrame(matrix.toarray(),
                        columns=vectorizer.get_feature_names(),
                        index=df.index)

words_df.head()

00 1241  00 1241 election  00 1241 election day  \
bill_name                                                          
Louisiana-HB167      0.0               0.0                   0.0   
izona-SB1003         0.0               0.0                   0.0   
kansas-HB1715        0.0               0.0                   0.0   
Wyoming-HB0075       0.0               0.0                   0.0   
Kansas hb2183        0.0               0.0                   0.0   

                 00 1241 election day the  00 23  00 23 for  00 23 for those  \
bill_name                                                                      
Louisiana-HB167                       0.0    0.0        0.0              0.0   
izona-SB1003                          0.0    0.0        0.0              0.0   
kansas-HB1715                         0.0    0.0        0.0              0.0   
Wyoming-HB0075                        0.0    0.0        0.0              0.0   
Kansas hb2183                         0.0    0.0        0.0              0.0   

                 00 23 for those persons  00 and  00 and before  ...  \
bill_name                                                        ...   
Louisiana-HB167                      0.0     0.0            0.0  ...   
izona-SB1003                         0.0     0.0            0.0  ...   
kansas-HB1715                        0.0     0.0            0.0  ...   
Wyoming-HB0075                       0.0     0.0            0.0  ...   
Kansas hb2183                        0.0     0.0            0.0  ...   

                 zone during polling hours  zone during polling hours 1238  \
bill_name                                                                    
Louisiana-HB167                        0.0                             0.0   
izona-SB1003                           0.0                             0.0   
kansas-HB1715                          0.0                             0.0   
Wyoming-HB0075                         0.0                             0.0   
Kansas hb2183                          0.0                             0.0   

                 zone regardless  zone regardless 21  zone regardless 21 of  \
bill_name                                                                     
Louisiana-HB167              0.0                 0.0                    0.0   
izona-SB1003                 0.0                 0.0                    0.0   
kansas-HB1715                0.0                 0.0                    0.0   
Wyoming-HB0075               0.0                 0.0                    0.0   
Kansas hb2183                0.0                 0.0                    0.0   

                 zone regardless 21 of the  zone such  zone such as  \
bill_name                                                             
Louisiana-HB167                        0.0        0.0           0.0   
izona-SB1003                           0.0        0.0           0.0   
kansas-HB1715                          0.0        0.0           0.0   
Wyoming-HB0075                         0.0        0.0           0.0   
Kansas hb2183                          0.0        0.0           0.0   

                 zone such as 1231  zone such as 1231 but  
bill_name                                                  
Louisiana-HB167                0.0                    0.0  
izona-SB1003                   0.0                    0.0  
kansas-HB1715                  0.0                    0.0  
Wyoming-HB0075                 0.0                    0.0  
Kansas hb2183                  0.0                    0.0  

[5 rows x 490227 columns]

### Let's narrow our pool of possible text reusers

* We'll use a similarity matrix!

In [16]:
from sklearn.metrics.pairwise import cosine_similarity

# Compute the similarities using the word counts
similarities = cosine_similarity(matrix)

# Make a fancy colored dataframe about it
similarity = pd.DataFrame(similarities, index=df.index, columns=df.index)

similarity.style.background_gradient(axis=None)

In [17]:
# Higher number implies maybe more reuse?
similarity.sum().sort_values(ascending=False)

bill_name
Indiana-SB0398       2.822433
Kentucky-HB574       2.809308
Georgia-SB202        2.754768
izona-SB1819         2.489560
izona-SB1485         2.436543
Kansas hb2332        2.387975
Kansas hb2183        2.321074
Iowa-SF568           2.237295
Iowa S.F. 413        2.174926
bama-HB538           2.115077
kansas-HB1715        2.093445
Oklahoma HB2663      2.079828
Montana-HB176        2.047043
kansas-SB643         2.033838
Montana-SB169        1.828839
izona-SB1003         1.816385
Florida S.B. 90      1.807610
Idaho HB 290         1.756620
Utah-HB0012          1.657634
Montana HB 530       1.591583
bama-HB285           1.534832
kansas-HB1244        1.533161
Wyoming-HB0075       1.507497
vada-SB84            1.448117
Louisiana-HB167      1.441705
Texas-HB3920         1.434681
w Hampshire-HB523    1.340421
dtype: float64

### ...and figure out what we want to use as our baseline

We'll use `IL-HB4066` because it seems to have some lines in common with other bills

In [18]:
similarity['Indiana-SB0398'].sort_values(ascending=False).head(20)

bill_name
Indiana-SB0398      1.000000
Georgia-SB202       0.152222
Kentucky-HB574      0.152128
Oklahoma HB2663     0.142067
izona-SB1819        0.110247
kansas-HB1715       0.109634
Kansas hb2183       0.109267
Kansas hb2332       0.104121
bama-HB538          0.099491
izona-SB1485        0.085769
Iowa-SF568          0.082561
Iowa S.F. 413       0.078655
kansas-SB643        0.074634
Montana-HB176       0.064339
Florida S.B. 90     0.056743
Idaho HB 290        0.048126
Utah-HB0012         0.047161
Montana-SB169       0.045523
izona-SB1003        0.042940
bama-HB285          0.034485
Name: Indiana-SB0398, dtype: float64

In [19]:
# Find the top 50 most similar, sorted by similarity
# and give me their bills numbers (they're the index)
# and then convert them into a list
# LET'S TAKE ALL OF THEM
most_similar = list(similarity['Indiana-SB0398'].sort_values(ascending=False).head(500).index)
most_similar[:5]

['Indiana-SB0398',
 'Georgia-SB202',
 'Kentucky-HB574',
 'Oklahoma HB2663 ',
 'izona-SB1819']

### Learn the phrases that are inside of IL-HB4066

These are the phrases we want to highlight - maybe we didn't use ngrams for similarity, but we're using ngrams down here for highlighting??? (for example)

In [20]:
bill_text = df.loc['Indiana-SB0398'].bill_text
bill_text[:100]

'First Regular Session of the 122nd General Assembly (2021)\n\nPRINTING CODE. Amendments: Whenever an e'

In [21]:
from sklearn.feature_extraction.text import CountVectorizer

# Find everything between 2-6 words
# and token_pattern means include things like "a" or "I" or "at"
vectorizer = CountVectorizer(ngram_range=(2,6), token_pattern='(?u)\\b\\w+\\b')

# Learn the words
vectorizer.fit([bill_text])
phrases = vectorizer.get_feature_names()
phrases[:10]

['00 a',
 '00 a m',
 '00 a m on',
 '00 a m on election',
 '00 a m on election day',
 '000 the',
 '000 the absentee',
 '000 the absentee voter',
 '000 the absentee voter board',
 '000 the absentee voter board in']

### Use the highlighter

In [22]:
# You can always cut and paste this code as long as you have 'phrases'

from rich.console import Console
from rich.highlighter import RegexHighlighter
from rich.theme import Theme

# You can run this code if you have a variable called
# "phrases" that is... the phrases you want to match.
class PhraseHighlighter(RegexHighlighter):
    base_style = "highlighter."
    highlights = [f"(?P<phrase>{phrase})" for phrase in phrases]

theme = Theme({"highlighter.phrase": "on pale_turquoise1"})
highlighter = Console(highlighter=PhraseHighlighter(), theme=theme)

In [24]:
for doc in most_similar:
    content = df.loc[doc].bill_text.lower() \
        .replace(".", "") \
        .replace(",", "") \
        .replace(";", "") \
        .replace('"', "") \
        .replace('“', "") \
        .replace('”', "") \
        .replace(")", "") \
        .replace("(", "")

    highlighter.print(f"[bold white on purple]{doc}[/bold white on purple]")
    highlighter.print(content)
    print("\n\n\n\n--------\n\n\n\n")

Indiana-SB0398

first regular session of the 122nd general assembly 2021

printing code amendments: whenever an existing statute or a section of the indiana
constitution is being amended the text of the existing provision will appear in this style 
type
additions will appear in this style type and deletions will appear in this style type
  additions: whenever a new statutory provision is being enacted or a new constitutional
provision adopted the text of the new provision will appear in  this  style  type also the
word new will appear in that style type in the introductory clause of each section that adds
a new provision to the indiana code or the indiana constitution
  conflict reconciliation: text in a statute in this style type or this style type reconciles
conflicts
between statutes enacted by the 2020 regular session of the general assembly

senate enrolled act no 398

an act to amend the indiana code concerning elections

be it enacted by the general assembly of the state of indiana:

section 1 ic 3-5-2-5 as amended by pl221-2005
section 4 is amended to read as follows [effective
july 1 2021]: sec 5 ballot label means any of the following:

1 the printed strip or sheet of cardboard or paper supplied for
use on an electronic voting system that contains the names of the
candidates and the public questions on the ballot or
2 the material supplied for use with a ballot card voting
system that contains those names and questions
3 the digital image of the ballot on the screen of an
electronic voting system or the interface of the marking device
used with an optical scan voting system

section 2 ic 3-5-2-31 as amended by pl71-2019
section 4 is amended to read as follows [effective
july 1 2021]: sec 31 a marking device means:

1 a pencil or pen for marking a paper ballot or ballot card or
2 an approved touch-sensitive device that automatically:

a registers a the voter's vote on an electronic voting system
or
b produces a marked optical scan ballot indicating the
choices of the voter

b a voter verifiable paper audit trail is not a marking device

sea 398 — concur



2

section 3 ic 3-5-2-503 is added to the indiana code
as a new section to read as follows [effective july
1 2021]: sec 503 voter with print disabilities means an
individual who is unable to independently mark a paper ballot or
ballot card due to blindness low vision or a physical disability that
impairs manual dexterity

section 4 ic 3-5-2-535 is added to the indiana code
as a new section to read as follows [effective july
1 2021]: sec 535 web content guidelines refers to version 21
of 





--------






Georgia-SB202

c:\pdf\201498wpd


21 sb 202/ap

s b 202
- 1 -

senate bill 202

by: senators burns of the 23rd miller of the 49th dugan of the 30th ginn of the 47th

anderson of the 24th and others 

as passed

a bill to be entitled

an act

to comprehensively revise elections and voting to amend chapter 2 of title 21 of the1

official code of georgia annotated relating to elections and primaries generally so as to2

revise a definition to provide for the establishment of a voter intimidation and illegal3

election activities hotline to limit the ability of the state election board and the 
secretary4

of state to enter into certain consent agreements settlements and consent orders to provide5

that the secretary of state shall be a nonvoting ex officio member of the state election6

board to provide for the appointment confirmation term and removal of the chairperson7

of the state election board to revise provisions relating to a quorum of such board to8

require the secretary of state to support and assist the state election board to provide for9

the appointment of temporary and permanent replacement superintendents to provide for10

procedures to provide for performance reviews of local election officials requested by the11

state election board or local governing authorities to provide for a definition to provide 
for12

appointment and duties of performance review boards to provide for reports of performance13

review boards to provide for promulgation of rules and regulations to provide additional14

requirements on the state election board's power to adopt emergency rules and regulations15

to provide that no election superintendents or boards of registrars shall accept private16

funding to provide that the state election board shall develop methods for distribution of17

donations to provide that certain persons may serve as poll workers in other than the 
county18



21 sb 202/ap

s b 202
- 2 -

of their residence to provide for the appointment of acting election superintendents in the19

event of a vacancy or incapacitation in the office of judge of the probate court of 
counties20

without a board of elections to provide for resumption of the duties of election21

superintendent upon the filling of such vacancy to provide for the compensation of such22

acting election superintendents to provide for the reduction in size of certain precincts 
under23

certain circumstances to provide for notice when polling places are relocated to provide 
for24

certain reports to provide limitations on the use of buses and other moveable facilities to25

provide that the name and designation of the precinct appears on every ballot to provide 
for26

allocation of voting equipment by counties and municipalities to provide for the manner of27

handling the death of a candidate prior to a nonpartisan election to provide that no 
candidate28

shall take or be sworn into any elected public office unless such candidate has received a29

majority of the votes cast for such office except as otherwise provided by law to provide 
for30

participation in a multistate voter registration system to revise procedures and standards 
for31

challenging electors to provide for the printing of ballots on safety paper to provide for 
the32

time and manner for applying for absentee ballots to provide for certain limitations and33

sanctions on the distribution of absentee ballot applications to provide for the manner of34

processing of absentee ballot applications to provide for absentee ballot drop boxes and 
the35

requirements therefor to provide for the time and manner of issuing absentee ballots to36

provide for the manner of voting and returning absentee ballots to revise the times for37

advance voting to limit changes to advance voting locations in the period prior to an38

election to provide notice requirements for changes of advance voting locations to provide39

for the processing and tabulation of absentee ballots to provide sanctions for improper

...

Kentucky-HB574

unofficial copy  21 rs hb 574/en 

page 1 of 168 
xxxx  engrossed 

an act relating to elections and making an appropriation therefor 1 

be it enacted by the general assembly of the commonwealth of kentucky: 2 

section 1   krs 83a045 is amended to read as follows: 3 

1 except as provided in krs 83a047 partisan elections of city officers shall be 4 

governed by the following provisions regardless of the form of government or 5 

classification of the city: 6 

a a candidate for party nomination to city office shall file his or her nomination 7 

papers with the county clerk of the county not earlier than the first wednesday 8 

after the first monday in november of the year preceding the year in which the 9 

office will appear on the ballot and not later than the first friday following the 10 

first monday in january before the day fixed by krs chapter 118 for holding 11 

a primary for the office sought signatures for nomination papers shall not be 12 

affixed on the document to be filed prior to the first wednesday after the first 13 

monday in november of the year preceding the year in which the office will 14 

appear on the ballot all nomination papers shall be filed no later than 4 pm 15 

local time when filed on the last day on which the papers are permitted to be 16 

filed 17 

b an independent candidate for nomination to city office shall not participate in 18 

a primary but shall file his or her nomination papers with the county clerk of 19 

the county not earlier than the first wednesday after the first monday in 20 

november of the year preceding the year in which the office will appear on 21 

the ballot and not later than the first tuesday after the first monday in june 22 

before the day fixed by krs chapter 118 for holding a regular election for the 23 

office signatures for nomination papers shall not be affixed on the document 24 

to be filed prior to the first wednesday after the first monday in november of 25 

the year preceding the year in which the office will appear on the ballot all 26 

nomination papers shall be filed no later than 4 pm local time when filed on 27 



unofficial copy  21 rs hb 574/en 

page 2 of 168 
xxxx  engrossed 

the last day on which the papers are permitted to be filed and 1 

c a candidate for city office who is defeated in a partisan primary shall be 2 

ineligible as a candidate for the same office in the regular election however 3 

if a vacancy occurs in the party nomination for which he or she was an 4 

unsuccessful candidate in the primary his or her name may be placed on the 5 

ballot for the regular election as a candidate of that party if 6 

he or she has been duly made the party nominee after the vacancy occurs as 7 

provided in krs 118105 8 

2 except as provided in krs 83a047 nonpartisan elections of city officers shall be 9 

governed by krs 83a050 83a170 83a175 and the following provisions 10 

regardless of the form of government or classification of the city: 11 

a a candidate for city office shall file his or her nomination papers with the 12 

county clerk of the county not earlier than the first wednesday after the first 13 

monday in november of the year preceding the year in which the office will 14 

appear on the ballot and not later than the first friday following the first 15 

monday in january before the day fixed by krs chapter 118 for holding a 16 

pr





--------






Oklahoma HB2663 

KeyboardInterrupt: 